
### Title: Homework6

### Author: Aishwarya Saibewar

### Date: 11/02/2023

In [1]:
#Import
import pandas as pd
import altair as alt

In [2]:
#Import the accident data for all the states in USA
us_accidents= pd.read_csv("/Users/aishwaryasaibewar/Documents/SeattleUniversity-MSDS/Courses/SU Course Work/FALL_2023/Data_Visualization/Class3/Homework3/US_Accidents_March23.csv")


In [3]:
#Find the shape of the data
us_accidents.shape

(7728394, 46)

In [4]:
#Downsample the data.
n = 3000  
us_accidents_downsampled = us_accidents.iloc[::n, :]
us_accidents_downsampled.shape

(2577, 46)

In [5]:
us_accidents_downsampled = us_accidents_downsampled.rename(columns={'Distance(mi)': 'distance_affected_by_accident'})

In [87]:
colors= alt.Scale(
    domain=['Cloudy','Fog','Rain','Fair'],
    range=['rgba(100, 149, 237, 0.7)', 'rgba(105, 105, 105, 0.9)', 'rgba(0, 0, 128, 1)', 'rgba(0, 128, 0, 0.3)']
  )
original= alt.Chart(us_accidents_downsampled).mark_line(point=True,clip=True,strokeWidth=4).transform_calculate(
    #Convert distance in miles to distance in feet
    Distance_in_feet='datum.distance_affected_by_accident * 5280',
    Number_of_vehicles_backlogged = 'datum.Distance_in_feet/36.7',
    Number_of_vehicles_backlogged_in_three_lanes = 'datum.Number_of_vehicles_backlogged * 3'

).transform_filter(
    alt.FieldOneOfPredicate(field='Weather_Condition', oneOf=['Cloudy','Fog','Rain','Fair'])
).transform_filter(
  alt.FieldOneOfPredicate(field='State', oneOf=["CA", "FL", "TX","NY","NC"])
).encode(
  alt.Y('median(Number_of_vehicles_backlogged_in_three_lanes):Q', title='Median of vehicles backlogged',scale=alt.Scale(domain=[0,400])),
  alt.X('month(Start_Time):N', title="Month"),
   alt.Color('Weather_Condition:N',title="Weather Condition", scale=colors)
  
)

# select a point for which to provide details-on-demand
label = alt.selection_single(
    encodings=['x'], # limit selection to x-axis value
    on='mouseover',  # select on mouseover events
    nearest=True,    # select data point nearest the cursor
    empty='none'     # empty selection includes no data points
)

final = alt.layer(
    original, 
    
    alt.Chart(us_accidents_downsampled).mark_rule(color='#aaa',clip=True).encode(
        x='month(Start_Time):N'
    ).transform_filter(label),
    
    # add circle marks for selected time points, hide unselected points
    original.mark_point(clip=True).encode(
        opacity=alt.condition(label, alt.value(1), alt.value(0))
    ).add_selection(label),
    
    # add white stroked text to provide a legible background for labels
    original.mark_text(align='left', dx=5, dy=-5, stroke='white', strokeWidth=7).encode(
        text=alt.Text('median(Number_of_vehicles_backlogged_in_three_lanes):Q', format='.1f')
    ).transform_filter(label),
    
    # add text labels for stock prices
    original.mark_text(align='left', dx=5, dy=-5,fontSize=13).encode(
        text=alt.Text('median(Number_of_vehicles_backlogged_in_three_lanes):Q', format='.1f')
    ).transform_filter(label)
).properties(
    title='Monthly median of vehicles  backlogged in various weathers',
    width=700,
    height=300
)

final

alt.LayerChart(...)

This multiline tooltip helps indicate the exact values of median vehicles backlogged for different weather conditions at the same time in a given month by simply dragging the tooltip across the x-axis.

In [89]:
colors= alt.Scale(
    domain=['Cloudy','Fog','Rain','Fair'],
    range=['rgba(100, 149, 237, 0.8)', 'rgba(105, 105, 105, 1)', 'rgba(0, 0, 128, 1.5)', 'rgba(0, 128, 0, 0.3)']
  )
original= alt.Chart(us_accidents_downsampled).mark_line(point=True,clip=True,strokeWidth=4).transform_calculate(
    #Convert distance in miles to distance in feet
    Distance_in_feet='datum.distance_affected_by_accident * 5280',
    Number_of_vehicles_backlogged = 'datum.Distance_in_feet/36.7',
    Number_of_vehicles_backlogged_in_three_lanes = 'datum.Number_of_vehicles_backlogged * 3'

).transform_filter(
    alt.FieldOneOfPredicate(field='Weather_Condition', oneOf=['Cloudy','Fog','Rain','Fair'])
).transform_filter(
  alt.FieldOneOfPredicate(field='State', oneOf=["CA", "FL", "TX","NY","NC"])
).encode(
  alt.Y('median(Number_of_vehicles_backlogged_in_three_lanes):Q', title='Median of vehicles backlogged',scale=alt.Scale(type='symlog',domain=[0,450])),
  alt.X('month(Start_Time):N', title="Month"),
   alt.Color('Weather_Condition:N',title="Weather Condition", scale=colors)
  
)

# select a point for which to provide details-on-demand
label = alt.selection_single(
    encodings=['x'], # limit selection to x-axis value
    on='mouseover',  # select on mouseover events
    nearest=True,    # select data point nearest the cursor
    empty='none'     # empty selection includes no data points
)

final = alt.layer(
    original, 
    
    alt.Chart(us_accidents_downsampled).mark_rule(color='#aaa',clip=True).encode(
        x='month(Start_Time):N'
    ).transform_filter(label),
    
    # add circle marks for selected time points, hide unselected points
    original.mark_point(clip=True).encode(
        opacity=alt.condition(label, alt.value(1), alt.value(0))
    ).add_selection(label),
    
    # add white stroked text to provide a legible background for labels
    original.mark_text(align='left', dx=5, dy=-5, stroke='white', strokeWidth=7).encode(
        text=alt.Text('median(Number_of_vehicles_backlogged_in_three_lanes):Q', format='.1f')
    ).transform_filter(label),
    
    # add text labels for stock prices
    original.mark_text(align='left', dx=5, dy=-5,fontSize=13).encode(
        text=alt.Text('median(Number_of_vehicles_backlogged_in_three_lanes):Q', format='.1f')
    ).transform_filter(label)
).properties(
    title='Monthly median of vehicles  backlogged in various weathers',
    width=700,
    height=300
)

final

alt.LayerChart(...)

In [91]:
final.save('accident_data.html')

In [92]:
with open("accident_data.html", "r") as html_file:
    html_content = html_file.read()
    
description = '''<!DOCTYPE html>
<html>
<head>
    <title>Monthly median of vehicles  backlogged in various weathers</title>
</head>
<body>
    <h1><center>Monthly median of vehicles  backlogged in various weathers</center></h1>
    <p>For this analysis, the top 5 accident-prone states have been considered. The median number of vehicles backlogged at the monthly level in various weather conditions was visualized using a line graph. In this plot, the variables in the order of importance are “Month” and “median number of vehicles backlogged”. The Nominal variable “Month” and the quantitative variable “median number of vehicles backlogged” are prioritized and given x and y position encoding, respectively. There are four categories for the "Weather Condition" Nominal variable: cloudy, fog, rain, and fair. As a result, the " Weather Condition" variable is least prioritized and is encoded using a color channel. As a result, each weather condition now has its unique color. Furthermore, the application of a "symlog" scale makes it easier to understand the specific value of median vehicles backlogged (in this case, the "symlog" scale is utilized in place of the "log" scale because, in a few months, there will be "0" median vehicles backlogged, and the log scale is inappropriate for values that include zero).</p>
    <p>The opacity of the lines was altered to improve the visual's accessibility for individuals with color blindness. The lines with varying opacities would become less transparent for the one with greater opacity and more transparent for the one with less opacity. This makes it easier for everyone, including those with disabilities, to distinguish between the various weather conditions. This can be verified using Google Chrome's Colorblindly extension (monochromacy specifically). </p>
    <p>Lastly, a rule with a multiline tooltip was added to determine the exact value of median vehicles backlogged for different weather conditions in a given month. Dragging the rule over the x-axis will reveal the precise values of the median vehicles backlogged for various weather conditions at the same time in a given month.</p>
</html>'''

html_content = html_content.replace('<body>', f'<body>\n{description}')

with open("accident_data.html", "w") as html_file:
    html_file.write(html_content)
    